In [132]:
import networkx as nx
from konlpy.tag import Okt
import collections
import matplotlib.pyplot as plt
from wordcloud import WordCloud
import pandas as pd
import time
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import linear_kernel
from sklearn.cluster import MiniBatchKMeans
from sklearn.metrics.pairwise import cosine_similarity

In [136]:
df = pd.read_csv('../../data/judicial_precedent_All_encoding.csv')[:500]
df.head()

판례일련번호                          사건명         사건번호        선고일자  법원명 사건종류명  \
0  238193                      손해배상(기)  2023다246600  2023.12.07  대법원    민사   
1  238199         근로기준법위반·근로자퇴직급여보장법위반   2020도15393  2023.12.07  대법원    형사   
2  238197                         건물인도  2022다279795  2023.12.07  대법원    민사   
3  238195  저작권법위반·부정경쟁방지및영업비밀보호에관한법률위반   2020도17863  2023.12.07  대법원    형사   
4  238191                      소유권이전등기  2023다269139  2023.12.07  대법원    민사   

     사건종류코드 판결유형  선고                                             판례상세링크  \
0  400101.0   판결  선고  /DRF/lawService.do?OC=dbs313&target=prec&ID=23...   
1  400102.0   판결  선고  /DRF/lawService.do?OC=dbs313&target=prec&ID=23...   
2  400101.0   판결  선고  /DRF/lawService.do?OC=dbs313&target=prec&ID=23...   
3  400102.0   판결  선고  /DRF/lawService.do?OC=dbs313&target=prec&ID=23...   
4  400101.0   판결  선고  /DRF/lawService.do?OC=dbs313&target=prec&ID=23...   

     법원종류코드                                               판시사항  \
0  400201.0    집합건물의 시공자의 분양자에 대한 하자보수를 갈음하는 손해배상채무의 소멸시효가 ...   
1  400201.0   [1] 구 근로기준법상 ‘1주간의 연장근로가 12시간을 초과하였는지’는 근로시간이...   
2  400201.0    [1] 임차인의 계약갱신 요구와 이를 거절할 수 있는 사유를 정한 주택임대차보호...   
3  400201.0   [1] 저작재산권 침해 여부를 가리기 위하여 두 저작물 사이에 실질적 유사성이 있...   
4  400201.0   [1] 당사자 사이에 계약의 해석을 둘러싸고 이견이 있어 당사자의 의사 해석이 문...   

                                                판결요지  \
0  집합건물의 소유 및 관리에 관한 법률(이하 ‘집합건물법’이라 한다) 제9조 제1항은...   
1  [1] 구 근로기준법(2017. 11. 28. 법률 제15108호로 개정되기 전의 ...   
2    [1] 2020. 7. 31. 법률 제17470호 개정으로 신설된 주택임대차보호...   
3   [1] 저작권법이 보호하는 것은 인간의 사상 또는 감정을 말·문자·음·색 등에 의...   
4   [1] 일반적으로 계약을 해석할 때에는 형식적인 문구에만 얽매여서는 안 되고 쌍방...   

                                                참조조문  \
0  집합건물의 소유 및 관리에 관한 법률 제9조 제1항, 제2항, 제3항, 민법 제66...   
1   [1] 구 근로기준법(2017. 11. 28. 법률 제15108호로 개정되기 전의...   
2   [1] 주택임대차보호법 제6조의3 제1항 / [2] 주택임대차보호법 제6조의3 제...   
3   [1] 저작권법 제136조 제1항 제1호 / [2] 저작권법 제20조, 제136조...   
4   [1] 민법 제105조 / [2] 민법 제536조 / [3] 민법 제2조 제1항,...   

                                                참조판례  \
0                                                NaN   
1   [1] 대법원 2013. 12. 18. 선고 2012다89399 전원합의체 판결(...   
2   [1] 대법원 2022. 12. 1. 선고 2021다266631 판결(공2023상...   
3   [1] 대법원 2010. 2. 11. 선고 2007다63409 판결(공2010상,...   
4   [1] 대법원 2021. 3. 25. 선고 2018다275017 판결(공2021상...   

                                                판례내용  
0  【원고, 피상고인】 ○○아파트 입주자대표회의 (소송대리인 법무법인 중추 담당변호사 ...  
1  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 신열...  
2  【원고, 피상고인】 원고<br/>【피고, 상고인】 피고 1 외 1인 (소송대리인 법...  
3  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 민...  
4  【원고, 상고인】 원고 (소송대리인 법무법인 지온 담당변호사 안민 외 1인)<br/...

In [138]:
df = df[df['사건종류명']=='형사']

df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 140 entries, 1 to 499
Data columns (total 16 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   판례일련번호  140 non-null    int64  
 1   사건명     140 non-null    object 
 2   사건번호    140 non-null    object 
 3   선고일자    140 non-null    object 
 4   법원명     140 non-null    object 
 5   사건종류명   140 non-null    object 
 6   사건종류코드  140 non-null    float64
 7   판결유형    140 non-null    object 
 8   선고      140 non-null    object 
 9   판례상세링크  140 non-null    object 
 10  법원종류코드  140 non-null    float64
 11  판시사항    122 non-null    object 
 12  판결요지    104 non-null    object 
 13  참조조문    122 non-null    object 
 14  참조판례    89 non-null     object 
 15  판례내용    140 non-null    object 
dtypes: float64(2), int64(1), object(13)
memory usage: 18.6+ KB


In [139]:
# df.info의 type이 object인 자료만 걸러냄
object_columns = df.select_dtypes(include=['object']).columns
object_columns

Index(['사건명', '사건번호', '선고일자', '법원명', '사건종류명', '판결유형', '선고', '판례상세링크', '판시사항',
       '판결요지', '참조조문', '참조판례', '판례내용'],
      dtype='object')

In [140]:
field = object_columns[4]
len(df[field].value_counts()), df[field].value_counts()

(1,
 형사    140
 Name: 사건종류명, dtype: int64)

In [87]:
cate=[]

for field in object_columns:
    print(field, '-->', len(df[field].value_counts()))

    if len(df[field].value_counts()<40):
        print()

사건명 --> 359

사건번호 --> 500

선고일자 --> 90

법원명 --> 28

사건종류명 --> 6

판결유형 --> 7

선고 --> 2

판례상세링크 --> 500

판시사항 --> 446

판결요지 --> 420

참조조문 --> 444

참조판례 --> 307

판례내용 --> 500



In [88]:
for field in object_columns:
    tmpData = df[field].value_counts()

In [90]:
numList = []
for num, x in enumerate(df['판례내용']):
    result = re.search(r'【이\s+유】\s*([^\n]*)', x)
    if result:
        extracted_text = result.group(1)
    cnt=len(extracted_text)
    if cnt<2:
        numList.append(num)

numList, len(numList)

([], 0)

In [142]:
df['이유']=df['판례내용'].str.split('【이    유】').str[1]
df.head()

판례일련번호                                                사건명        사건번호  \
1   238199                               근로기준법위반·근로자퇴직급여보장법위반  2020도15393   
3   238195                        저작권법위반·부정경쟁방지및영업비밀보호에관한법률위반  2020도17863   
10  238201                                             저작권법위반  2020도10180   
12  238025                                             특수재물손괴  2023도11885   
13  238023  공직선거법위반[공직선거법상 예비후보자에게 허용되는 선거운동방법 중 하나인 ‘표지물을...   2023도5915   

          선고일자  법원명 사건종류명    사건종류코드 판결유형  선고  \
1   2023.12.07  대법원    형사  400102.0   판결  선고   
3   2023.12.07  대법원    형사  400102.0   판결  선고   
10  2023.11.30  대법원    형사  400102.0   판결  선고   
12  2023.11.16  대법원    형사  400102.0   판결  선고   
13  2023.11.16  대법원    형사  400102.0   판결  선고   

                                               판례상세링크    법원종류코드  \
1   /DRF/lawService.do?OC=dbs313&target=prec&ID=23...  400201.0   
3   /DRF/lawService.do?OC=dbs313&target=prec&ID=23...  400201.0   
10  /DRF/lawService.do?OC=dbs313&target=prec&ID=23...  400201.0   
12  /DRF/lawService.do?OC=dbs313&target=prec&ID=23...  400201.0   
13  /DRF/lawService.do?OC=dbs313&target=prec&ID=23...  400201.0   

                                                 판시사항  \
1    [1] 구 근로기준법상 ‘1주간의 연장근로가 12시간을 초과하였는지’는 근로시간이...   
3    [1] 저작재산권 침해 여부를 가리기 위하여 두 저작물 사이에 실질적 유사성이 있...   
10  저작권법 제136조 제2항 제1호 위반죄에서 저작자 또는 실연자의 ‘명예’의 의미(...   
12  [1] 민법 제256조에서 부동산에의 부합의 예외사유로 규정한 ‘권원’의 의미 / ...   
13  [1] 공직선거법 제60조의3 제1항 제5호에 따라 예비후보자에게 허용되는 선거운동...   

                                                 판결요지  \
1   [1] 구 근로기준법(2017. 11. 28. 법률 제15108호로 개정되기 전의 ...   
3    [1] 저작권법이 보호하는 것은 인간의 사상 또는 감정을 말·문자·음·색 등에 의...   
10  저작권법 제136조 제2항 제1호는 저작인격권 또는 실연자의 인격권을 침해하여 저작...   
12  [1] 민법 제256조에서 부동산에의 부합의 예외사유로 규정한 ‘권원’은 지상권, ...   
13  [1] 공직선거법 제60조의3 제1항 제5호에 따라 예비후보자에게 허용되는 선거운동...   

                                                 참조조문  \
1    [1] 구 근로기준법(2017. 11. 28. 법률 제15108호로 개정되기 전의...   
3    [1] 저작권법 제136조 제1항 제1호 / [2] 저작권법 제20조, 제136조...   
10                            저작권법 제136조 제2항 제1호<br/>   
12   [1] 민법 제256조, 형법 제366조 / [2] 형법 제366조, 제369조 ...   
13   [1] 공직선거법 제60조의3 제1항 제5호 / [2] 공직선거법 제60조의3 제...   

                                                 참조판례  \
1    [1] 대법원 2013. 12. 18. 선고 2012다89399 전원합의체 판결(...   
3    [1] 대법원 2010. 2. 11. 선고 2007다63409 판결(공2010상,...   
10               대법원 2009. 5. 28. 선고 2007다354 판결<br/>   
12   [1] 대법원 2005. 1. 27. 선고 2004도6289 판결, 대법원 201...   
13                                                NaN   

                                                 판례내용  \
1   【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 신열...   
3   【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 민...   
10  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 린...   
12  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 박남...   
13  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 하...   

                                                   이유  
1     상고이유를 판단한다.<br/>  1. 공소사실의 요지와 원심의 판단<br/>  ...  
3     상고이유를 판단한다.<br/>  1. 제1 상고이유에 관하여<br/>  가. 저...  
10    상고이유를 판단한다. <br/>  1. 저작권법 제136조 제2항 제1호는 저작...  
12    상고이유를 판단한다.<br/>  1. 사실오인 및 심리미진 여부<br/>  이 ...  
13    상고이유를 판단한다.<br/>  1. 공직선거법 제60조의3 제1항 제5호(이하...

In [143]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 140 entries, 1 to 499
Data columns (total 17 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   판례일련번호  140 non-null    int64  
 1   사건명     140 non-null    object 
 2   사건번호    140 non-null    object 
 3   선고일자    140 non-null    object 
 4   법원명     140 non-null    object 
 5   사건종류명   140 non-null    object 
 6   사건종류코드  140 non-null    float64
 7   판결유형    140 non-null    object 
 8   선고      140 non-null    object 
 9   판례상세링크  140 non-null    object 
 10  법원종류코드  140 non-null    float64
 11  판시사항    122 non-null    object 
 12  판결요지    104 non-null    object 
 13  참조조문    122 non-null    object 
 14  참조판례    89 non-null     object 
 15  판례내용    140 non-null    object 
 16  이유      140 non-null    object 
dtypes: float64(2), int64(1), object(14)
memory usage: 23.8+ KB


In [144]:
df_re = df[['판례내용', '이유']].dropna()
df_re

판례내용  \
1    【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 신열...   
3    【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 민...   
10   【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 린...   
12   【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 박남...   
13   【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 하...   
..                                                 ...   
494  【피 고 인】 피고인<br/>【상 고 인】 검사<br/>【변 호 인】 법무법인 해랑...   
495  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 장성...   
496  【피 고 인】 피고인<br/>【항 소 인】 검사<br/>【검    사】 권예리 외 ...   
498  【피 고 인】 피고인<br/>【상 고 인】 검사<br/>【원심판결】 의정부지법 20...   
499  【피 고 인】 피고인<br/>【상 고 인】 검사<br/>【변 호 인】 변호사 박규철...   

                                                    이유  
1      상고이유를 판단한다.<br/>  1. 공소사실의 요지와 원심의 판단<br/>  ...  
3      상고이유를 판단한다.<br/>  1. 제1 상고이유에 관하여<br/>  가. 저...  
10     상고이유를 판단한다. <br/>  1. 저작권법 제136조 제2항 제1호는 저작...  
12     상고이유를 판단한다.<br/>  1. 사실오인 및 심리미진 여부<br/>  이 ...  
13     상고이유를 판단한다.<br/>  1. 공직선거법 제60조의3 제1항 제5호(이하...  
..                                                 ...  
494    상고이유를 판단한다.<br/>  1. 「교통사고처리 특례법」위반(치상)의 점에 ...  
495    1. 상고이유를 판단한다.<br/>상고법원은 상고이유에 의하여 불복신청한 한도 ...  
496    1. 항소이유의 요지<br/>  가. 판단유탈<br/>  이 사건 공소사실 중 ...  
498    상고이유를 판단한다.<br/>형법 제49조 단서는 ‘행위자에게 유죄의 재판을 하...  
499    상고이유를 판단한다.<br/>  1. 형법상 절취란 타인이 점유하고 있는 자기 ...  

[140 rows x 2 columns]

In [145]:
ps_list = []
okt = Okt()

for r in df_re['이유']:
    ps = okt.pos(r)
    ps_list.append(ps)

ps_list

[[('상고', 'Noun'),
  ('이유', 'Noun'),
  ('를', 'Josa'),
  ('판단', 'Noun'),
  ('한다', 'Verb'),
  ('.<', 'Punctuation'),
  ('br', 'Alpha'),
  ('/>', 'Punctuation'),
  ('1', 'Number'),
  ('.', 'Punctuation'),
  ('공', 'Modifier'),
  ('소', 'Modifier'),
  ('사실', 'Noun'),
  ('의', 'Josa'),
  ('요지', 'Noun'),
  ('와', 'Josa'),
  ('원심', 'Noun'),
  ('의', 'Josa'),
  ('판단', 'Noun'),
  ('<', 'Punctuation'),
  ('br', 'Alpha'),
  ('/>', 'Punctuation'),
  ('가', 'Verb'),
  ('.', 'Punctuation'),
  ('연장', 'Noun'),
  ('근로', 'Noun'),
  ('제한', 'Noun'),
  ('위반', 'Noun'),
  ('으로', 'Josa'),
  ('인한', 'Adjective'),
  ('근로기준법', 'Noun'),
  ('위반', 'Noun'),
  ('의', 'Josa'),
  ('공소', 'Noun'),
  ('사실', 'Noun'),
  ('요지', 'Noun'),
  ('<', 'Punctuation'),
  ('br', 'Alpha'),
  ('/>', 'Punctuation'),
  ('이', 'Noun'),
  ('부분', 'Noun'),
  ('공', 'Modifier'),
  ('소', 'Modifier'),
  ('사실', 'Noun'),
  ('의', 'Josa'),
  ('요지', 'Noun'),
  ('는', 'Josa'),
  (',', 'Punctuation'),
  ('피고인', 'Noun'),
  ('이', 'Josa'),
  ('상시', 'Noun'),
  ('500',

In [146]:
result = []
for poss in ps_list:
    pos_list = []
    for p in poss:
        if (p[1]=='Noun') or (p[1]=='Adjective'):
            pos_list.append(p[0])
    result.append(pos_list)

result

[['상고',
  '이유',
  '판단',
  '사실',
  '요지',
  '원심',
  '판단',
  '연장',
  '근로',
  '제한',
  '위반',
  '인한',
  '근로기준법',
  '위반',
  '공소',
  '사실',
  '요지',
  '이',
  '부분',
  '사실',
  '요지',
  '피고인',
  '상시',
  '명의',
  '근로자',
  '사용',
  '이',
  '사건',
  '회사',
  '대표이사',
  '로서',
  '근로자',
  '소외',
  '주간',
  '초과',
  '연장',
  '근로',
  '내용',
  '나',
  '원심',
  '판단',
  '원심',
  '취업규칙',
  '및',
  '근로계약서',
  '상의',
  '시업',
  '시각',
  '업무',
  '일지',
  '상의',
  '업무',
  '종료',
  '시각',
  '사이',
  '시간',
  '중',
  '휴게',
  '시간',
  '제외',
  '나머지',
  '시간',
  '모두',
  '실',
  '근로시간',
  '해당',
  '고',
  '전제',
  '후',
  '소외',
  '주간',
  '근로시간',
  '중',
  '근로',
  '일',
  '초과',
  '근로시간',
  '합산',
  '해당',
  '주의',
  '위',
  '합산',
  '시간',
  '초과',
  '주간',
  '연장',
  '근로시간',
  '한도',
  '정',
  '구',
  '근로기준법',
  '법률',
  '제',
  '호로',
  '개정',
  '전의',
  '것',
  '이하',
  '같다',
  '제',
  '제',
  '항',
  '위반',
  '보아',
  '이',
  '사건',
  '공소',
  '사실',
  '중',
  '대하',
  '유죄',
  '나머지',
  '이유',
  '무죄',
  '로',
  '인정',
  '제',
  '심',
  '판단',
  '유지',
  '대법원',
  '판단',
  '관련',
  '법리',
  '구

In [147]:
df_re['Adj-Noun'] = result
df_re

판례내용  \
1    【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 신열...   
3    【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 민...   
10   【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 린...   
12   【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 박남...   
13   【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 하...   
..                                                 ...   
494  【피 고 인】 피고인<br/>【상 고 인】 검사<br/>【변 호 인】 법무법인 해랑...   
495  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 장성...   
496  【피 고 인】 피고인<br/>【항 소 인】 검사<br/>【검    사】 권예리 외 ...   
498  【피 고 인】 피고인<br/>【상 고 인】 검사<br/>【원심판결】 의정부지법 20...   
499  【피 고 인】 피고인<br/>【상 고 인】 검사<br/>【변 호 인】 변호사 박규철...   

                                                    이유  \
1      상고이유를 판단한다.<br/>  1. 공소사실의 요지와 원심의 판단<br/>  ...   
3      상고이유를 판단한다.<br/>  1. 제1 상고이유에 관하여<br/>  가. 저...   
10     상고이유를 판단한다. <br/>  1. 저작권법 제136조 제2항 제1호는 저작...   
12     상고이유를 판단한다.<br/>  1. 사실오인 및 심리미진 여부<br/>  이 ...   
13     상고이유를 판단한다.<br/>  1. 공직선거법 제60조의3 제1항 제5호(이하...   
..                                                 ...   
494    상고이유를 판단한다.<br/>  1. 「교통사고처리 특례법」위반(치상)의 점에 ...   
495    1. 상고이유를 판단한다.<br/>상고법원은 상고이유에 의하여 불복신청한 한도 ...   
496    1. 항소이유의 요지<br/>  가. 판단유탈<br/>  이 사건 공소사실 중 ...   
498    상고이유를 판단한다.<br/>형법 제49조 단서는 ‘행위자에게 유죄의 재판을 하...   
499    상고이유를 판단한다.<br/>  1. 형법상 절취란 타인이 점유하고 있는 자기 ...   

                                              Adj-Noun  
1    [상고, 이유, 판단, 사실, 요지, 원심, 판단, 연장, 근로, 제한, 위반, 인...  
3    [상고, 이유, 판단, 제, 상고, 이유, 관, 저작권법, 보호, 것, 인간, 사상...  
10   [상고, 이유, 판단, 저작권법, 제, 제, 항, 제, 호, 저작인격권, 실연자, ...  
12   [상고, 이유, 판단, 사실, 오인, 및, 심리, 미진, 여부, 이, 부분, 상고,...  
13   [상고, 이유, 판단, 공직선거법, 제, 제, 항, 제, 호, 이하, 이, 사건, ...  
..                                                 ...  
494  [상고, 이유, 판단, 교통사고, 처리, 특례법, 위반, 치, 의, 점, 관, 원심...  
495  [상고, 이유, 판단, 상고, 법원, 상고, 이유, 의하여, 불복신청, 한도, 내,...  
496  [항소, 이유, 요지, 판단, 유탈, 이, 사건, 공소, 사실, 중, 업무, 과실,...  
498  [상고, 이유, 판단, 형법, 제, 단서, 행위자, 유죄, 재판, 아니, 때, 몰수...  
499  [상고, 이유, 판단, 형법, 절취, 란, 타인, 점유, 있는, 자기, 이외, 자의...  

[140 rows x 3 columns]

In [148]:
str = []
for ans in df_re['Adj-Noun']:
    an = ' '.join(ans)
    str.append(an)

str        

['상고 이유 판단 사실 요지 원심 판단 연장 근로 제한 위반 인한 근로기준법 위반 공소 사실 요지 이 부분 사실 요지 피고인 상시 명의 근로자 사용 이 사건 회사 대표이사 로서 근로자 소외 주간 초과 연장 근로 내용 나 원심 판단 원심 취업규칙 및 근로계약서 상의 시업 시각 업무 일지 상의 업무 종료 시각 사이 시간 중 휴게 시간 제외 나머지 시간 모두 실 근로시간 해당 고 전제 후 소외 주간 근로시간 중 근로 일 초과 근로시간 합산 해당 주의 위 합산 시간 초과 주간 연장 근로시간 한도 정 구 근로기준법 법률 제 호로 개정 전의 것 이하 같다 제 제 항 위반 보아 이 사건 공소 사실 중 대하 유죄 나머지 이유 무죄 로 인정 제 심 판단 유지 대법원 판단 관련 법리 구 근로기준법 제 주간 근로시간 휴게 시간 제외 초과 수 없고 제 항 근로시간 휴게 시간 제외 초과 수 없다 제 항 고 규정 제 제 항 당사자 간 합의 주간 한도 제 근로시간 연장 수 있다고 규정 있다 구 근로기준법 제 제 항 연장 근로시간 한도 주간 기준 설정 있을 뿐 기준 삼고 있지 아니하므로 주간 연장 근로 초과 근로시간 초과 고려 주간 근로시간 중 초과 근로시간 기준 판단 그 이유 다음 같다 구 근로기준법 제 제 항 주 단위 연장 근로 한도 설정 있으므로 여기 말 연장 로란 같은 법 제 제 항의 주간 의 기준 근로시간 초과 근로 의미 해석 것 자연스럽다 구 근로기준법 제 제 항 제 근로시간 연장 수 있다고 규정 제 제 항의 근로시간 규율 대상 포함 것 당사자 간 합의 초과 연장 근로 가능하다는 의미 연장 근로 한도 별도 규제 의미 아니다 나 구 근로기준법 주간 주간 연장 근로시간 제한 기준 규정 탄력 근로시간 제나 선택 근로 시간제 등 있으나 제 제 항 제 제 초과 연장 근로시간 주간 합계 관 정 있는 규정 없다 초과 거나 주간 초과 연장 근로 대해 통상 임금 이상 가산 임금 지급 정 있는데 구 근로기준법 제 연장 근로 대하 가산 임금 지급 규정 사용자 금전 부담 연장 근로 억제 한편 연장

In [149]:
df_re['str'] = str
df_re

판례내용  \
1    【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 신열...   
3    【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 민...   
10   【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 린...   
12   【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 박남...   
13   【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 하...   
..                                                 ...   
494  【피 고 인】 피고인<br/>【상 고 인】 검사<br/>【변 호 인】 법무법인 해랑...   
495  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 장성...   
496  【피 고 인】 피고인<br/>【항 소 인】 검사<br/>【검    사】 권예리 외 ...   
498  【피 고 인】 피고인<br/>【상 고 인】 검사<br/>【원심판결】 의정부지법 20...   
499  【피 고 인】 피고인<br/>【상 고 인】 검사<br/>【변 호 인】 변호사 박규철...   

                                                    이유  \
1      상고이유를 판단한다.<br/>  1. 공소사실의 요지와 원심의 판단<br/>  ...   
3      상고이유를 판단한다.<br/>  1. 제1 상고이유에 관하여<br/>  가. 저...   
10     상고이유를 판단한다. <br/>  1. 저작권법 제136조 제2항 제1호는 저작...   
12     상고이유를 판단한다.<br/>  1. 사실오인 및 심리미진 여부<br/>  이 ...   
13     상고이유를 판단한다.<br/>  1. 공직선거법 제60조의3 제1항 제5호(이하...   
..                                                 ...   
494    상고이유를 판단한다.<br/>  1. 「교통사고처리 특례법」위반(치상)의 점에 ...   
495    1. 상고이유를 판단한다.<br/>상고법원은 상고이유에 의하여 불복신청한 한도 ...   
496    1. 항소이유의 요지<br/>  가. 판단유탈<br/>  이 사건 공소사실 중 ...   
498    상고이유를 판단한다.<br/>형법 제49조 단서는 ‘행위자에게 유죄의 재판을 하...   
499    상고이유를 판단한다.<br/>  1. 형법상 절취란 타인이 점유하고 있는 자기 ...   

                                              Adj-Noun  \
1    [상고, 이유, 판단, 사실, 요지, 원심, 판단, 연장, 근로, 제한, 위반, 인...   
3    [상고, 이유, 판단, 제, 상고, 이유, 관, 저작권법, 보호, 것, 인간, 사상...   
10   [상고, 이유, 판단, 저작권법, 제, 제, 항, 제, 호, 저작인격권, 실연자, ...   
12   [상고, 이유, 판단, 사실, 오인, 및, 심리, 미진, 여부, 이, 부분, 상고,...   
13   [상고, 이유, 판단, 공직선거법, 제, 제, 항, 제, 호, 이하, 이, 사건, ...   
..                                                 ...   
494  [상고, 이유, 판단, 교통사고, 처리, 특례법, 위반, 치, 의, 점, 관, 원심...   
495  [상고, 이유, 판단, 상고, 법원, 상고, 이유, 의하여, 불복신청, 한도, 내,...   
496  [항소, 이유, 요지, 판단, 유탈, 이, 사건, 공소, 사실, 중, 업무, 과실,...   
498  [상고, 이유, 판단, 형법, 제, 단서, 행위자, 유죄, 재판, 아니, 때, 몰수...   
499  [상고, 이유, 판단, 형법, 절취, 란, 타인, 점유, 있는, 자기, 이외, 자의...   

                                                   str  
1    상고 이유 판단 사실 요지 원심 판단 연장 근로 제한 위반 인한 근로기준법 위반 공...  
3    상고 이유 판단 제 상고 이유 관 저작권법 보호 것 인간 사상 감정 말 문자 음 색...  
10   상고 이유 판단 저작권법 제 제 항 제 호 저작인격권 실연자 인격권 침해 저작자 실...  
12   상고 이유 판단 사실 오인 및 심리 미진 여부 이 부분 상고 이유 형사소송법 제 제...  
13   상고 이유 판단 공직선거법 제 제 항 제 호 이하 이 사건 조항 의하여 예비 후보자...  
..                                                 ...  
494  상고 이유 판단 교통사고 처리 특례법 위반 치 의 점 관 원심 그 같은 이유 이 사...  
495  상고 이유 판단 상고 법원 상고 이유 의하여 불복신청 한도 내 조사 판단 수 있으므...  
496  항소 이유 요지 판단 유탈 이 사건 공소 사실 중 업무 과실 부분 내용 피고인 팁 ...  
498  상고 이유 판단 형법 제 단서 행위자 유죄 재판 아니 때 몰수 요건 있는 때 몰수 ...  
499  상고 이유 판단 형법 절취 란 타인 점유 있는 자기 이외 자의 유물 점유 의사 반하...  

[140 rows x 4 columns]

In [150]:
df_re.to_csv('tostr.csv', index=False)

In [151]:
df = pd.read_csv('tostr.csv')
df.head()

판례내용  \
0  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 신열...   
1  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 민...   
2  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 린...   
3  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 변호사 박남...   
4  【피 고 인】 피고인<br/>【상 고 인】 피고인<br/>【변 호 인】 법무법인 하...   

                                                  이유  \
0    상고이유를 판단한다.<br/>  1. 공소사실의 요지와 원심의 판단<br/>  ...   
1    상고이유를 판단한다.<br/>  1. 제1 상고이유에 관하여<br/>  가. 저...   
2    상고이유를 판단한다. <br/>  1. 저작권법 제136조 제2항 제1호는 저작...   
3    상고이유를 판단한다.<br/>  1. 사실오인 및 심리미진 여부<br/>  이 ...   
4    상고이유를 판단한다.<br/>  1. 공직선거법 제60조의3 제1항 제5호(이하...   

                                            Adj-Noun  \
0  ['상고', '이유', '판단', '사실', '요지', '원심', '판단', '연장...   
1  ['상고', '이유', '판단', '제', '상고', '이유', '관', '저작권법...   
2  ['상고', '이유', '판단', '저작권법', '제', '제', '항', '제',...   
3  ['상고', '이유', '판단', '사실', '오인', '및', '심리', '미진'...   
4  ['상고', '이유', '판단', '공직선거법', '제', '제', '항', '제'...   

                                                 str  
0  상고 이유 판단 사실 요지 원심 판단 연장 근로 제한 위반 인한 근로기준법 위반 공...  
1  상고 이유 판단 제 상고 이유 관 저작권법 보호 것 인간 사상 감정 말 문자 음 색...  
2  상고 이유 판단 저작권법 제 제 항 제 호 저작인격권 실연자 인격권 침해 저작자 실...  
3  상고 이유 판단 사실 오인 및 심리 미진 여부 이 부분 상고 이유 형사소송법 제 제...  
4  상고 이유 판단 공직선거법 제 제 항 제 호 이하 이 사건 조항 의하여 예비 후보자...

In [152]:
start_time = time.time()
text_content = df['str']
vector = TfidfVectorizer(max_df=0.4,                # 전체 문서에서 40% 이상 등장하는 단어는 무시
                             min_df=1,              # 최소 1회 이상 등장 단어만 사용
                             stop_words='english',  # 영어의 불용어를 적용
                             lowercase=True,        # 전체 소문자로 변환
                             use_idf=True,          # IDF를 가중치에 적용
                             norm=u'l2',            # 유클리드 노름을 사용하여 정규화
                             smooth_idf=True        # Zero divide 에러를 방지하기 위해 IDF에 스무딩 적용
                            )
tfidf = vector.fit_transform(text_content)

In [158]:
k = 10
kmeans = MiniBatchKMeans(n_clusters = k)
kmeans.fit(tfidf)
centers = kmeans.cluster_centers_.argsort()[:,::-1]
terms = vector.get_feature_names()

    
request_transform = vector.transform(df['str'])
# new column cluster based on the description
df['cluster'] = kmeans.predict(request_transform) 
df['cluster'].value_counts().head()

0    46
3    31
1    19
5    11
7    10
Name: cluster, dtype: int64

In [159]:
def find_similar(tfidf_matrix, index, top_n = 5):
    cosine_similarities = linear_kernel(tfidf_matrix[index:index+1], tfidf_matrix).flatten()
    related_docs_indices = [i for i in cosine_similarities.argsort()[::-1] if i != index]
    return [index for index in related_docs_indices][0:top_n]  

In [ ]:
G = nx.Graph(label="Judical")
start_time = time.time()
for i, rowi in df.iterrows():
    if (i%1000==0):
        print(" iter {} -- {} seconds --".format(i,time.time() - start_time))
    G.add_node(rowi['title'],key=rowi['show_id'],label="MOVIE",mtype=rowi['type'],rating=rowi['rating'])
#    G.add_node(rowi['cluster'],label="CLUSTER")
#    G.add_edge(rowi['title'], rowi['cluster'], label="DESCRIPTION")


판례내용에서 '이유' 이후만 별도의 자료로 만들고  
명사와 형용사만 토큰화 시킨 후 문자열(str)로 제작하여 tf-idf에 넣을 자료를 작성한 후  
csv로 저장하여 다시 불러온다  
tf-idf를 이용하여 질문에 대한 비슷한 판례내용을 추천하고  
네트워크 그래프를 작성한다(단, 사건 종류 중 형사 사건에 대해서)  